# Analysis of fluorescent microplastic particles

In this Jupyter Notebook you can find all relevant spectral analysis of the recorded spectra

In [116]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D

from scipy.signal import find_peaks, peak_prominences

from typing import Optional, Tuple, Dict

import plotly.graph_objects as go

import pandas as pd

from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.discriminant_analysis import LinearDiscriminantAnalysis as LDA
from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_score, silhouette_samples

color_dict = {
    'PP-pure': 'aqua', 
    'PP-yellow': 'yellow',
    'PP-green': 'chartreuse',
    'PP-orange': 'darkorange',
    'PP-pink': 'deeppink'
}

data_dict = np.load("data_dict.npy", allow_pickle=True).item()
wavelengths = np.load("wavelengths.npy")

markers = ["v", "s", "o", "^", "D", "P", "X", "*"]
marker_dict = {cls: markers[i % len(markers)] for i, cls in enumerate(data_dict.keys())}

markersize = 50
alpha_pts = 0.85


In [ ]:
laser_end = 460     # Startwavelength for peak search in spectra

top_n = 30          # Number of top peaks to find in spectra sums

sample_list = ['PP-yellow', 'PP-green', 'PP-orange', 'PP-pink'] # Sample choice --- EDIT ---
# sample_list = 'all'

if sample_list == 'all':
    sample_list = list(data_dict.keys())                        # List of sample names  
sample_number = len(sample_list)

# Wavelength indices for intensity ratios

I0 = np.argwhere(wavelengths >= 614.3)[0][0]    
I1 = np.argwhere(wavelengths >= 495.8)[0][0]
I2 = np.argwhere(wavelengths >= 580.1)[0][0]
I3 = np.argwhere(wavelengths >= 466.9)[0][0]

In [118]:
def norm_spectra(
    wavelengths: np.ndarray,
    spectrum: np.ndarray,
    indices: np.ndarray,
    laser_end: float = 460.0,
    norm_choice: str = "minmax"   # minmax | zscore | auc
    ) -> Tuple[np.ndarray, np.ndarray, np.ndarray]:
    """
    Normalizes the spectrum and calculates the wavelengths and indices of the maximum value.

    Returns:
      Tuple with normalized spectrum, wavelengths, and indices of the maximum value
    """
    mask = (wavelengths > laser_end)
    n_spectra = spectrum.shape[0]
    normed_spectrum = np.empty_like(spectrum, dtype=float)
    
    if norm_choice == "minmax":
        min_vals = spectrum.min(axis=1, keepdims=True)
        max_vals = spectrum[:, mask].max(axis=1, keepdims=True)
        normed_spectrum = (spectrum - min_vals) / (max_vals - min_vals)
    elif norm_choice == "zscore":
        mean_vals = spectrum[:, mask].mean(axis=1, keepdims=True)
        std_vals = spectrum[:, mask].std(axis=1, keepdims=True)
        normed_spectrum = (spectrum - mean_vals) / std_vals
    elif norm_choice == "auc":
        auc = np.array([np.trapezoid(spectrum[i][mask], wavelengths[mask]) for i in range(n_spectra)])
        normed_spectrum = spectrum / auc[:, np.newaxis] * mask.sum()
    else:
        raise ValueError(f"Unknown normalization method: {norm_choice}")

    max_indices = spectrum[:, indices].argmax(axis=1, keepdims=True) + indices[0]
    max_wavelengths = wavelengths[max_indices]
    return normed_spectrum, max_wavelengths, max_indices

def mean_and_std(data: np.ndarray) -> Tuple[float, float]:
    """
    Calculates the mean and standard deviation of the given data.

    Args:
    data: Input data as a numpy array.

    Returns:
    A tuple containing the mean and standard deviation of the input data.
    """
    mean = np.mean(data)
    std = np.std(data, ddof=1)  # Sample standard deviation
    return mean, std

def fwhm_and_bounds(
    wavelengths: np.ndarray,
    spectrum: np.ndarray,
    max_index: np.ndarray
    ) -> Tuple[float, float, float, float, float, float, float, float]:
    """
    Calculates the full width at half maximum (FWHM) and the left and right half maximum wavelengths (with interpolation).

    Args:
    wavelengths: Wavelengths corresponding to the spectrum.
    spectrum: The spectrum as a numpy array.
    max_index: Index of the maximum value in the spectrum.

    Returns:
    A tuple containing the FWHM, lambda left, lambda right including all values and mean/std.
    """
    fwhm = np.empty(spectrum.shape[0])
    left_half_max = np.empty(spectrum.shape[0])
    right_half_max = np.empty(spectrum.shape[0])

    for i in range(len(spectrum)):
        idx_max = max_index[i][0]
        half_max = spectrum[i][idx_max] / 2

        # Search for the left crossing (from maximum to lower indices)
        left = np.where(spectrum[i][:idx_max] < half_max)[0]
        if left.size == 0:
            left_wl = wavelengths[0]
        else:
            l1 = left[-1]
            l2 = l1 + 1
            # Linear interpolation between l1 and l2 for subpixel accuracy
            x1, x2 = wavelengths[l1], wavelengths[l2]
            y1, y2 = spectrum[i][l1], spectrum[i][l2]
            left_wl = x1 + (half_max - y1) * (x2 - x1) / (y2 - y1)

        # Search for the right crossing (from maximum to higher indices)
        right = np.where(spectrum[i][idx_max:] < half_max)[0]
        if right.size == 0:
            right_wl = wavelengths[-1]
        else:
            r1 = idx_max + right[0] - 1
            r2 = r1 + 1
            if r2 >= len(wavelengths):
                right_wl = wavelengths[-1]
            else:
                x1, x2 = wavelengths[r1], wavelengths[r2]
                y1, y2 = spectrum[i][r1], spectrum[i][r2]
                right_wl = x1 + (half_max - y1) * (x2 - x1) / (y2 - y1)

        fwhm[i] = right_wl - left_wl
        left_half_max[i] = left_wl
        right_half_max[i] = right_wl

    fwhm_mean, fwhm_std = mean_and_std(fwhm)
    left_half_max_mean, left_half_max_std = mean_and_std(left_half_max)
    right_half_max_mean, right_half_max_std = mean_and_std(right_half_max)

    return fwhm, left_half_max, right_half_max, fwhm_mean, fwhm_std, left_half_max_mean, left_half_max_std, right_half_max_mean, right_half_max_std

In [119]:
spectra_array = np.empty((sample_number), dtype=object)         # Array to hold all spectra

color_list = [color_dict[sample] for sample in sample_list]     # List of colors for samples

spectra_dict = {}                                               # Dictionary to hold spectra

spectra_sums = np.empty_like(spectra_array)                     # Array to hold sum of spectra
normed_spectra_sums = np.empty_like(spectra_array)              # Array to hold normalized sum of spectra

sum_peaks = np.empty_like(spectra_array)                        # Array to hold peaks of summed spectra
spectra_peaks = np.empty_like(spectra_array)                    # Array to hold spectra behind peaks of summed spectra

normed_spectra_peaks = np.empty_like(spectra_array)             # Array to hold normalized spectra behind peaks of summed spectra
normed_spectra_peaks_mean = np.empty_like(spectra_array)        # Array to hold mean normalized spectra behind peaks of summed spectra
normed_spectra_peaks_max = np.empty_like(spectra_array)         # Array to hold max normalized spectra behind peaks of summed spectra
normed_spectra_peaks_min = np.empty_like(spectra_array)         # Array to hold min normalized spectra behind peaks of summed spectra

lambda_max_array = np.empty_like(spectra_array)                 # Array to hold wavelengths of peaks
max_indices = np.empty_like(spectra_array)                      # Array to hold indices of peaks

I_max_array = np.empty_like(spectra_array)                      # Array to hold intensities at emission maxima
FWHM_array = np.empty_like(spectra_array)                       # Array to hold full width at half maximum
left_half_max_array = np.empty_like(spectra_array)              # Array to hold left half maximum
right_half_max_array = np.empty_like(spectra_array)             # Array to hold right half maximum

lambda_max_mean_std = np.empty((sample_number, 2), dtype=object)         # Array to hold mean and sample variance of wavelengths of emission maxima
I_max_mean_std = np.empty((sample_number, 2), dtype=object)              # Array to hold mean and sample variance of intensities at emission maxima
FWHM_mean_std = np.empty((sample_number, 2), dtype=object)               # Array to hold mean and sample variance of full width at half maximum
left_half_max_mean_std = np.empty((sample_number, 2), dtype=object)      # Array to hold mean and sample variance of left half maximum
right_half_max_mean_std = np.empty((sample_number, 2), dtype=object)     # Array to hold mean and sample variance of right half maximum

R1_array = np.empty_like(spectra_array)                         # Array to hold intensity ratio 1
R2_array = np.empty_like(spectra_array)                         # Array to hold intensity ratio 2

## Calculation of relevant spectral parameters

In [120]:
wavelengths_indices = np.argwhere(wavelengths > laser_end).flatten()

i = 0
for sample, spectra in data_dict.items():
    if sample in sample_list:
        # Get spectra and calculate sum of spectra
        spectra_array[i] = spectra
        spectra_sums[i] = np.array([spectrum.sum() for spectrum in spectra])
        normed_spectra_sums[i] = spectra_sums[i] / np.max(spectra_sums[i])
        
        # Find peaks in summed spectra
        sum_peaks[i], properties = find_peaks(normed_spectra_sums[i], prominence = 0.1)
        prominences = peak_prominences(normed_spectra_sums[i], sum_peaks[i])[0]

        # Sort peaks by prominence and select top_n peaks
        sorted_indices = np.argsort(prominences)[::-1]
        sorted_peaks = sum_peaks[i][sorted_indices]
        sorted_prominences = prominences[sorted_indices]

        # Select top_n peaks
        spectra_peaks[i] = spectra_array[i][sorted_peaks[:top_n]]

        # Add spectra behind peaks to dictionary
        for j in range(len(spectra_peaks[i])):
            spectra_dict[f"{sample}_{str(j+1).zfill(3)}"] = spectra_peaks[i][j]

        # Normalize spectra behind peaks and calculate wavelengths and indices of max value
        normed_spectra_peaks[i], lambda_max_array[i], max_indices[i] = norm_spectra(wavelengths, spectra_peaks[i], wavelengths_indices, laser_end, norm_choice="minmax")

        # Calculate mean, max, and min of normalized spectra behind peaks
        normed_spectra_peaks_mean[i] = normed_spectra_peaks[i].mean(axis=0)
        normed_spectra_peaks_max[i] = normed_spectra_peaks[i].max(axis=0)
        normed_spectra_peaks_min[i] = normed_spectra_peaks[i].min(axis=0)

        # Calculate wavelengths at emission maxima, intensities at maxima, FWHM, left and right half max
        lambda_max_mean_std[i][0], lambda_max_mean_std[i][1] = mean_and_std(lambda_max_array[i])
        I_max_array[i] = np.array([spectra_peaks[i][j, max_indices[i][j]] for j in range(spectra_peaks[i].shape[0])])
        I_max_mean_std[i][0], I_max_mean_std[i][1] = mean_and_std(np.array([spectra_peaks[i][j, max_indices[i][j]] for j in range(spectra_peaks[i].shape[0])]))
        FWHM_array[i], left_half_max_array[i], right_half_max_array[i], FWHM_mean_std[i][0], FWHM_mean_std[i][1], left_half_max_mean_std[i][0], left_half_max_mean_std[i][1], right_half_max_mean_std[i][0], right_half_max_mean_std[i][1] = fwhm_and_bounds(wavelengths, normed_spectra_peaks[i], max_indices[i])

        # Calculate intensity ratios
        R1_array[i] = normed_spectra_peaks[i][:,I1]/normed_spectra_peaks[i][:,I0]
        R2_array[i] = normed_spectra_peaks[i][:,I2]/normed_spectra_peaks[i][:,I3]

        i += 1

## Spectra of different polypropylene samples

In [121]:
fig = go.Figure()

for i in range(sample_number):
    for j in range(len(normed_spectra_peaks[i])):
        trace_name = f"{sample_list[i]} {j+1}"
        fig.add_trace(go.Scatter(
            x=wavelengths,
            y=normed_spectra_peaks[i][j],
            mode='lines',
            line=dict(color=color_list[i], width=1),
            opacity=0.2,
            name=trace_name,
            legendgroup=sample_list[i],
            showlegend=False,
            visible=True
        ))
    # Add invisible trace for legend entry
    # This trace is visible in the legend and controls all related traces via legendgroup.
    fig.add_trace(go.Scatter(
        x=[wavelengths[0]], 
        y=[np.nan],                 
        mode='lines',
        line=dict(color=color_list[i], width=3),
        opacity=1.0,
        name=sample_list[i],
        legendgroup=sample_list[i],
        showlegend=True,
        visible=True
    ))

fig.update_layout(
    width=1000,
    height=600,
    xaxis_title='Wavelength (nm)',
    yaxis_title='Normalised Counts (a.u.)',
    yaxis=dict(range=[-0.1, 1.1],
               showline=True, 
               linewidth=1, 
               linecolor='black', 
               mirror=True, 
               ticks='outside',),
    xaxis=dict(range=[370, 925],
               showline=True, linewidth=1, linecolor='black', mirror=True, ticks='outside'),
    plot_bgcolor='white',
    paper_bgcolor='white',
    legend=dict(title='Class', itemclick='toggle'),  
    template='simple_white',
    margin=dict(l=80, r=40, t=40, b=60)
)

fig.show()

## Spectral parameters

In [122]:
data_mean_std = {
    "Sample": sample_list,
    "λ_max (nm)": lambda_max_mean_std[:,0],
    "λ_max std (nm)": lambda_max_mean_std[:,1],
    "I_max (a.u.)": I_max_mean_std[:,0],
    "I_max std (a.u.)": I_max_mean_std[:,1],
    "FWHM (nm)": FWHM_mean_std[:,0],
    "FWHM std (nm)": FWHM_mean_std[:,1],
    "λ_left (nm)": left_half_max_mean_std[:,0],
    "λ_left std (nm)": left_half_max_mean_std[:,1],
    "λ_right (nm)": right_half_max_mean_std[:,0],
    "λ_right std (nm)": right_half_max_mean_std[:,1],
}

data_complete = {
    "Sample": sample_list,
    "λ_max (nm)": lambda_max_array,
    "I_max (a.u.)": I_max_array,
    "FWHM (nm)": FWHM_array,
    "λ_left (nm)": left_half_max_array,
    "λ_right (nm)": right_half_max_array
}
df_complete = pd.DataFrame(data_complete)
df_mean_std = pd.DataFrame(data_mean_std)
pd.set_option('display.precision', 1)
display(df_mean_std)

Sample λ_max (nm) λ_max std (nm) I_max (a.u.) I_max std (a.u.)  \
0  PP-yellow      499.4            1.0       7933.8           5549.0   
1   PP-green      502.3            4.5        964.8            699.6   
2  PP-orange      584.3            0.4      18275.5          12390.1   
3    PP-pink      589.9            1.9       1040.7            709.9   

  FWHM (nm) FWHM std (nm) λ_left (nm) λ_left std (nm) λ_right (nm)  \
0      57.8           1.0       482.5             1.1        540.3   
1      56.5           5.7       480.5             1.8        537.0   
2      39.4           0.3       568.0             0.3        607.4   
3      37.9           1.6       573.9             1.0        611.8   

  λ_right std (nm)  
0              1.3  
1              5.1  
2              0.4  
3              1.0

In [123]:
# Erstelle DataFrame aus deinem Dictionary
df_complete = pd.DataFrame(data_complete)

# Liste der spektralen Parameter für den Schalter
param_names = [
    "λ_max (nm)",
    "I_max (a.u.)",
    "FWHM (nm)",
    "λ_left (nm)",
    "λ_right (nm)"
]

# Boxplot-Traces für jeden Parameter, alle unsichtbar außer dem ersten
traces = []
for idx, param in enumerate(param_names):
    # Werte ggf. flatten, falls sie nicht 1D sind
    y = np.concatenate([np.ravel(vals) for vals in df_complete[param].values])
    x = np.concatenate([[sample]*len(np.ravel(vals)) for sample, vals in zip(df_complete["Sample"], df_complete[param])])
    traces.append(
        go.Box(
            y=y,
            x=x,
            name=param,
            visible=(idx == 0),
            boxmean='sd'
        )
    )

# Dropdown-Buttons
buttons = []
for idx, param in enumerate(param_names):
    visible = [False] * len(param_names)
    visible[idx] = True
    buttons.append(
        dict(
            label=param,
            method="update",
            args=[
                {"visible": visible},
                {
                    "yaxis": {
                        "title": param,
                        "showline": True,
                        "linewidth": 1,
                        "linecolor": "black",
                        "mirror": True,
                        "ticks": "outside"
                    },
                    "xaxis": {
                        "showline": True,
                        "linewidth": 1,
                        "linecolor": "black",
                        "mirror": True,
                        "ticks": "outside"
                    }
                }
            ]
        )
    )

fig = go.Figure(data=traces)
fig.update_layout(
    updatemenus=[
        dict(
            type="dropdown",
            direction="down",
            buttons=buttons,
            x=1.15,
            y=1.05,
            showactive=True,
        )
    ],
    yaxis=dict(showline=True, linewidth=1, linecolor='black', mirror=True, ticks='outside'),
    xaxis=dict(showline=True, linewidth=1, linecolor='black', mirror=True, ticks='outside'),
    yaxis_title=param_names[0],
    xaxis_title="Sample",
    width=1000,
    height=600,
    boxmode='group',
    template='simple_white',
    margin=dict(l=60, r=40, t=40, b=60)
)

fig.show()

## Clustering via intensity ratios

In [124]:
_marker_map = {'s':'square', 'o':'circle', '^':'triangle-up', 'D':'diamond','v':'triangle-down','P':'pentagon','X':'x','*':'star'}

fig = go.Figure()

for i in range(sample_number):
    symbol = _marker_map.get(marker_dict[sample_list[i]], 'circle')
    labels = [f"{sample_list[i]} {k+1}" for k in range(len(R1_array[i]))]
    fig.add_trace(go.Scatter(
        x = R1_array[i],
        y = R2_array[i],
        mode = 'markers',
        name = sample_list[i],
        marker = dict(
            symbol = symbol,
            size = markersize/5,                 
            color = color_list[i],
            opacity = alpha_pts,
            line = dict(color='black', width=1)  
        ),
        hovertemplate = "%{text}<br>R1: %{x}<br>R2: %{y}<extra></extra>",
        text = labels
    ))

fig.update_layout(
    width = 1000,
    height = 600,
    xaxis = dict(
        title = r'R1',
        ticks = 'outside',
        showgrid = True,
        gridcolor = 'rgba(0,0,0,0.08)',
        minor = dict(dtick=1, showgrid=True, gridcolor='rgba(0,0,0,0.04)'),
        showline=True, linewidth=1, linecolor='black', mirror=True
    ),
    yaxis = dict(
        title = r'R2',
        type = 'log',
        showgrid = True,
        gridcolor = 'rgba(0,0,0,0.08)',
        minor = dict(showgrid=True, gridcolor='rgba(0,0,0,0.04)'),
        showline=True, linewidth=1, linecolor='black', mirror=True
    ),
    template = 'simple_white',
    legend = dict(title='Class', itemclick='toggle'),
    margin = dict(l=80, r=40, t=40, b=60)
)

fig.show()

### Silhouette score for clustering via intensity ratios

In [125]:
# Prepare data - combine all R1 and R2 values
R1_all = np.concatenate([R1_array[i] for i in range(sample_number)])
R2_all = np.concatenate([np.log(R2_array[i]) for i in range(sample_number)])

# Create labels for the true classes
true_labels = []
for i, sample in enumerate(sample_list):
    true_labels.extend([i] * len(R1_array[i]))
true_labels = np.array(true_labels)

# Create feature matrix
X = np.column_stack([R1_all, R2_all])

# Optional: standardize data
scaler = StandardScaler()
X_scaled = scaler.fit_transform(X)

# Silhouette score per sample class
sample_silhouette_values = silhouette_samples(X_scaled, true_labels, metric='euclidean')

sil_df = pd.DataFrame(columns=['class', 'silhouette score'])

sample_score_list = []

# Average silhouette score per sample
for i, sample in enumerate(sample_list):
    sample_mask = (true_labels == i)
    sample_score = sample_silhouette_values[sample_mask].mean()
    sample_score_list.append(sample_score)

# Silhouette score for the 4 true sample classes
sil_df['class'] = sample_list + ['Overall']
true_silhouette = silhouette_score(X_scaled, true_labels)
sample_score_list += [true_silhouette]
sil_df['silhouette score'] = sample_score_list

pd.set_option('display.precision', 3)
display(sil_df)

class  silhouette score
0  PP-yellow             0.800
1   PP-green             0.585
2  PP-orange             0.854
3    PP-pink             0.757
4    Overall             0.749

## Numerical clustering

In [126]:
# Convert data to DataFrame
spectra_df = pd.DataFrame.from_dict(spectra_dict, orient='index')
# Set Multiindex with class and sample key
spectra_df.index.name = 'sample_key'
spectra_df.insert(0, 'class', spectra_df.index.map(lambda x: x.split('_')[0]))
spectra_df = spectra_df.reset_index()
spectra_df = spectra_df.set_index(['class', 'sample_key'])
# Sort by class
spectra_df = spectra_df.sort_index(level='class')

In [127]:
# Select classes to analyze
classes = sample_list
# Filter DataFrame for selected classes
spectra_df = spectra_df[spectra_df.index.get_level_values('class').isin(classes)]
# Normalize spectra
spectra_df = spectra_df.mul(spectra_df.shape[1]).div(spectra_df.sum(axis=1), axis=0)
# Create DataFrame with scaled spectra
scaled_spectra_df = pd.DataFrame(
  StandardScaler().fit_transform(spectra_df),
  index=spectra_df.index,
  columns=spectra_df.columns
)

In [128]:
n_components = 12
n_samples = spectra_df.shape[0]

print(f"Number of components: {n_components if n_components < n_samples else n_samples}, Number of samples: {n_samples}")

pca = PCA(n_components=n_components if n_components < n_samples else n_samples, whiten=True, random_state=42)
pc_df = pd.DataFrame(pca.fit_transform(scaled_spectra_df), index=spectra_df.index)

lda = LDA(solver='svd')
ld_df = pd.DataFrame(lda.fit_transform(pc_df, pc_df.index.get_level_values('class')), index=pc_df.index)
ld_df = ld_df.rename(columns=lambda x: f'LD{x+1}').reset_index()
ld_df['class'] = pd.Categorical(ld_df['class'], categories=sample_list, ordered=True)
ld_df = ld_df.sort_values('class')

Number of components: 12, Number of samples: 120


In [129]:
_marker_map = {'s':'square', 'o':'circle', '^':'triangle-up', 'D':'diamond','v':'triangle-down','P':'pentagon','X':'x','*':'star'}

fig = go.Figure()

for cls, sub in ld_df.groupby('class', observed=True):
    symbol = _marker_map.get(marker_dict[cls], 'circle')

    fig.add_trace(go.Scatter(
        x=sub['LD1'],
        y=sub['LD2'],
        mode='markers',
        name=cls,
        marker=dict(
            symbol = symbol,
            size = markersize/5,
            color = color_dict.get(cls, 'C0'),
            opacity = alpha_pts,
            line = dict(color='black', width=1)  
        ),
        text=[f"{cls} {i+1}" for i in range(len(sub))],
        hovertemplate="%{text}<br>LD1: %{x:.2f}<br>LD2: %{y:.2f}<extra></extra>"
    ))
    i += 1

fig.update_layout(
    width=1000,
    height=600,
    xaxis=dict(
        title='LD1',
        ticks='outside',
        showgrid=True,
        gridcolor='rgba(0,0,0,0.08)',
        minor=dict(dtick=1, showgrid=True, gridcolor='rgba(0,0,0,0.04)'),
        showline=True, linewidth=1, linecolor='black', mirror=True
    ),
    yaxis=dict(
        title='LD2',
        type='linear',
        showgrid=True,
        gridcolor='rgba(0,0,0,0.08)',
        minor=dict(showgrid=True, gridcolor='rgba(0,0,0,0.04)'),
        showline=True, linewidth=1, linecolor='black', mirror=True
    ),
    template='simple_white',
    legend=dict(title='Class', itemclick='toggle'),
    margin=dict(l=80, r=40, t=40, b=60)
)

fig.show()

### LDA explained variance ratio

In [130]:
# Plot LDA explained variance
evr = getattr(lda, "explained_variance_ratio_", None)


x = np.arange(1, len(evr) + 1)
explained_var = evr * 100
cumulative_var = np.cumsum(evr) * 100

fig = go.Figure()

# Balken für explained variance
fig.add_trace(go.Bar(
    x=[f"LD{i}" for i in x],
    y=explained_var,
    name="Explained variance",
    marker_color="steelblue"
))

# Linie für cumulative explained variance
fig.add_trace(go.Scatter(
    x=[f"LD{i}" for i in x],
    y=cumulative_var,
    mode="lines+markers",
    name="Cumulative",
    line=dict(color="black"),
    marker=dict(symbol="circle", color="black")
))

fig.update_layout(
    width=1000,
    height=600,
    xaxis_title="Linear Discriminant",
    yaxis_title="Explained variance (%)",
    xaxis=dict(
        showline=True,
        linewidth=1,
        linecolor='black',
        mirror=True,
        tickmode='array',
        tickvals=[f"LD{i}" for i in x],
        ticktext=[f"LD{i}" for i in x]
    ),
    yaxis=dict(
        showline=True,
        linewidth=1,
        linecolor='black',
        mirror=True,
        showgrid=True,
        gridcolor='rgba(0,0,0,0.08)'
    ),
    legend=dict(itemclick='toggle'),
    template='simple_white',
    margin=dict(l=60, r=40, t=60, b=60)
)

fig.show()

print(f"LDA explained variance using LD1 and LD2: {evr[0] + evr[1]}")
if evr is None:
    raise AttributeError("LDA has no explained_variance_ratio_. Ensure solver='svd' and that lda is fitted.")

LDA explained variance using LD1 and LD2: 0.8604989187359431


### Silhouette score for combined PCA and LDA

In [131]:
ld_cols = [c for c in ld_df.columns if c.startswith("LD")][:2]
X_ld = ld_df[ld_cols].values
true_labels = ld_df["class"].values

scaler = StandardScaler()
X_scaled = scaler.fit_transform(X_ld)

sil_score = silhouette_score(X_ld, true_labels, metric="euclidean")

sil_samples = silhouette_samples(X_ld, true_labels, metric="euclidean")

df = pd.DataFrame()
df['class'] = true_labels
df['silhouette score'] = sil_samples
means = df.groupby('class', observed=True)['silhouette score'].mean()
pd.set_option('display.precision', 3)
means_df = means.reset_index()
means_df.loc[len(means_df)] = ['Overall', sil_score]
display(means_df)

class  silhouette score
0  PP-yellow             0.849
1   PP-green             0.812
2  PP-orange             0.894
3    PP-pink             0.879
4    Overall             0.859